репул чтобы 500 не было 

In [1]:
#500 fixed
import gymnasium as gym
from gymnasium import spaces

class TicTacToeEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    
    symbols = ['O', ' ', 'X']

    def __init__(self):
        self.action_space = spaces.Discrete(9)
        self.observation_space = spaces.Discrete(9*3*2) # flattened
    def step(self, action):
        done = False

        p, square = action
        
        # check move legality
        board = self.state['board']
        proposed = board[square]
        player = self.state['on_move']
        if (proposed != 0):  # wrong player, not empty
            print("illegal move ", action, ". (square occupied): ", square)
            done = True
        if (p != player):  # wrong player, not empty
            print("illegal move  ", action, " not on move: ", p)
            done = True
        else:
            board[square] = p
            self.state['on_move'] = -p

        # check game over
        for i in range(3):
            # horizontals and verticals
            if ((board[i * 3] == p and board[i * 3 + 1] == p and board[i * 3 + 2] == p)
                or (board[i + 0] == p and board[i + 3] == p and board[i + 6] == p)):
                done = True
                break
        # diagonals
        if((board[0] == p and board[4] == p and board[8] == p)
            or (board[2] == p and board[4] == p and board[6] == p)):
                done = True
                
        return self.state, done, {}
    def reset(self):
        self.state = {}
        self.state['board'] = [0, 0, 0, 0, 0, 0, 0, 0, 0]
        self.state['on_move'] = 1
        return self.state
    def render(self, mode='human', close=False):
        if close:
            return
        print("on move: " , self.symbols[self.state['on_move']+1])
        for i in range (9):
            print (self.symbols[self.state['board'][i]+1], end=" ")
            if ((i % 3) == 2):
                print()
    def move_generator(self):
        moves = []
        for i in range (9):
            if (self.state['board'][i] == 0):
                p = self.state['on_move']
                m = [p, i]
                moves.append(m)
        return moves
    

Ключевые функции Gymnasium:¶
self.reset() — инициализация среды.

self.step(action) — выполнение действия и переход в новое состояние.

self.render() — визуализация текущего состояния среды.

Реализация агента¶
Агент принимает решение (выбирает действие), основываясь на текущем состоянии среды, и затем получает обратную связь (награду и новое состояние) от среды.

Функции агента:¶
Выбор действия: Использует алгоритмы или стратегии, чтобы определить, что делать дальше.

Обучение: Обновляет свои знания или стратегию на основе опыта, чтобы лучше справляться с задачей.

Интерактивность: Адаптируется к изменениям в среде.


In [9]:
import random

class MyAgent:
    def __init__(self, symbol):
        self.symbol = symbol  # Символ игрока (1 - X, -1 - O)
    
    def get_action(self, moves):
        return random.choice(moves)  # Выбор случайного хода из доступных

Цикл обучения

In [10]:
# Создание среды для игры в крестики-нолики
myenv = TicTacToeEnv()

# Создание агента
agent = MyAgent(symbol=1)

num_episodes = 50  # Количество эпизодов (игр) для обучения
collected_rewards = []      # Список для хранения наград/побед в каждом эпизоде 

# Переменная для отслеживания символа и текущего игрока
current_player = 1

for i in range(num_episodes):
    # Сброс среды и начало нового эпизода
    state, _ = myenv.reset() 

    # Общая награда за эпизод
    total_reward = 0

    # Флаг завершения игры
    done = False
    player = current_player 

    # Максимум 9 ходов, поскольку поле 3x3 
    for j in range(9): 
        moves = myenv.move_generator() 

        # Ходов нет, заканчиваем игру
        if not moves:
            break

        
        if len(moves) == 1:
            move = moves[0]    
        else:
            move = agent.get_action(moves)   

        # Выполнение хода и обновление состояния игры
        next_state, done, info = myenv.step(move)
        state = next_state

        # Отображаем текущее состояние игры
        myenv.render()

        if done:
            break

        player = -player    # Смена игрока

    print(f"Episode {i+1} is done")

on move:  O
      
    X 
      
on move:  X
  O   
    X 
      
on move:  O
  O   
    X 
  X   
on move:  X
  O   
    X 
  X O 
on move:  O
  O X 
    X 
  X O 
on move:  X
  O X 
  O X 
  X O 
on move:  O
X O X 
  O X 
  X O 
on move:  X
X O X 
  O X 
O X O 
on move:  O
X O X 
X O X 
O X O 
Episode 1 is done
on move:  O
      
      
  X   
on move:  X
      
O     
  X   
on move:  O
      
O     
X X   
on move:  X
  O   
O     
X X   
on move:  O
  O X 
O     
X X   
on move:  X
O O X 
O     
X X   
on move:  O
O O X 
O X   
X X   
Episode 2 is done
on move:  O
X     
      
      
on move:  X
X   O 
      
      
on move:  O
X   O 
X     
      
on move:  X
X O O 
X     
      
on move:  O
X O O 
X     
X     
Episode 3 is done
on move:  O
      
X     
      
on move:  X
O     
X     
      
on move:  O
O X   
X     
      
on move:  X
O X   
X   O 
      
on move:  O
O X X 
X   O 
      
on move:  X
O X X 
X O O 
      
on move:  O
O X X 
X O O 
  X   
on move:  X
O X X 
X O